In [13]:
import spacy

In [14]:
nlp = spacy.load("fr_core_news_sm")

In [21]:
text = "je veux aller de Paris à Roissy en Brie"

In [22]:
doc = nlp(text)

In [23]:
for token in doc:
    if token.dep_ == "prep":
        print(f"Préposition : {token.text} → {token.head.text}")

In [24]:
for entity in doc.ents:
    print(f"Entité de lieu : {entity.text}")

Entité de lieu : Paris
Entité de lieu : Roissy
Entité de lieu : Brie


In [25]:
for token in doc:
    print(f"{token} -> {token.dep_}")

je -> nsubj
veux -> ROOT
aller -> xcomp
de -> case
Paris -> obl:arg
à -> case
Roissy -> obl:mod
en -> case
Brie -> obl:mod


In [8]:
import pandas as pd

In [9]:
df = pd.read_csv('fake_data.csv')

In [10]:
df.head()

sentence       ville_origine  \
0  Aller de Paris Saint-Lazare à Saint-Dié-des-Vo...  Paris Saint-Lazare   
1               Voyage reliant Lille CHR et La Fère.           Lille CHR   
2            Route entre Juan les Pins et Renescure.       Juan les Pins   
3  Par où passer pour aller de Neufchâteau à Le C...         Neufchâteau   
4            Je me déplace de Lisieux vers Langeais.             Lisieux   

          ville_arrivee  
0  Saint-Dié-des-Vosges  
1               La Fère  
2             Renescure  
3   Le Cateau-Cambrésis  
4              Langeais

In [13]:
for sentence in df["sentence"]:
    print(sentence)
    doc = nlp(sentence)
    print(doc)
    for entity in doc.ents:
        print(f"{entity.text} -> {entity.label_}")
    print("\n")

Aller de Paris Saint-Lazare à Saint-Dié-des-Vosges.
Aller de Paris Saint-Lazare à Saint-Dié-des-Vosges.
Paris Saint-Lazare -> LOC
Saint-Dié-des-Vosges -> LOC


Voyage reliant Lille CHR et La Fère.
Voyage reliant Lille CHR et La Fère.
Lille CHR -> ORG
La Fère -> LOC


Route entre Juan les Pins et Renescure.
Route entre Juan les Pins et Renescure.
Juan les Pins -> LOC
Renescure -> PER


Par où passer pour aller de Neufchâteau à Le Cateau-Cambrésis ?
Par où passer pour aller de Neufchâteau à Le Cateau-Cambrésis ?
Neufchâteau -> PER
Le Cateau-Cambrésis -> MISC


Je me déplace de Lisieux vers Langeais.
Je me déplace de Lisieux vers Langeais.
Lisieux -> LOC
Langeais -> LOC


Comment aller de Orry-la-Ville - Coye à Jarrie - Vizille ?
Comment aller de Orry-la-Ville - Coye à Jarrie - Vizille ?


Au départ de Avenue Foch jusqu’à Domont.
Au départ de Avenue Foch jusqu’à Domont.
Avenue Foch jusqu’ -> PER
Domont -> LOC


Je cherche à me rendre de La Guierche à Crêches-sur-Saône.
Je cherche à me ren

In [11]:
def compute_score(row):
    doc = nlp(row["sentence"])
    ents = {ent.text.lower() for ent in doc.ents}
    matches = sum(city.lower() in ents for city in [row["ville_origine"], row["ville_arrivee"]])
    return matches / 2

df["entity_match_score"] = df.apply(compute_score, axis=1)
df[["sentence", "ville_origine", "ville_arrivee", "entity_match_score"]].head()

sentence       ville_origine  \
0  Aller de Paris Saint-Lazare à Saint-Dié-des-Vo...  Paris Saint-Lazare   
1               Voyage reliant Lille CHR et La Fère.           Lille CHR   
2            Route entre Juan les Pins et Renescure.       Juan les Pins   
3  Par où passer pour aller de Neufchâteau à Le C...         Neufchâteau   
4            Je me déplace de Lisieux vers Langeais.             Lisieux   

          ville_arrivee  entity_match_score  
0  Saint-Dié-des-Vosges                 1.0  
1               La Fère                 1.0  
2             Renescure                 1.0  
3   Le Cateau-Cambrésis                 1.0  
4              Langeais                 1.0

In [12]:
df[df["entity_match_score"] != 1]

sentence  \
5      Comment aller de Orry-la-Ville - Coye à Jarrie...   
6               Au départ de Avenue Foch jusqu’à Domont.   
8                  Route Villefranche-sur-Cher Baisieux.   
9      Comment effectuer le trajet entre Paris Bercy ...   
10     Le Chambon-Feugerolles vers Le Meux - La Croix...   
...                                                  ...   
19991                        Route Montreuil Montaudran.   
19992  Je prévois d’aller à Carnoles depuis Clelles -...   
19994              Aller de Vaas à Pierrefitte - Stains.   
19996     Route entre Remise à Jorelle et Méry-sur-Oise.   
19997  Quel moyen permet de relier La Fouillouse à De...   

                                 ville_origine                  ville_arrivee  \
5                         Orry-la-Ville - Coye               Jarrie - Vizille   
6                                  Avenue Foch                         Domont   
8                        Villefranche-sur-Cher                       Baisieux   
9      Paris Bercy Bourgogne - Pays d'Auvergne         Maresquel-Ecquemicourt   
10                      Le Chambon-Feugerolles  Le Meux - La Croix-Saint-Ouen   
...                                        ...                            ...   
19991                                Montreuil                     Montaudran   
19992                           Clelles - Mens                       Carnoles   
19994                                     Vaas           Pierrefitte - Stains   
19996                         Remise à Jorelle                  Méry-sur-Oise   
19997                            La Fouillouse              Deuil - Montmagny   

       entity_match_score  
5                     0.0  
6                     0.5  
8                     0.0  
9                     0.0  
10                    0.0  
...                   ...  
19991                 0.0  
19992                 0.5  
19994                 0.0  
19996                 0.5  
19997                 0.5  

[9363 rows x 4 columns]